In [1]:
import numpy as np
import pandas as pd
import os
from datetime import datetime, timedelta
import alpaca_trade_api as tradeapi
%matplotlib inline
from alpha_vantage.timeseries import TimeSeries
import plotly.express as px
import hvplot.pandas
import panel as pn
import seaborn as sns
from pathlib import Path
import seaborn as sb
pn.extension("plotly")
end_date=datetime.now().strftime('%Y-%m-%d')
import pandas_datareader.data as data

# -----------------------------------------------------------------------

# Xavier's work

### Entertainment
* etf = xly (Consumer Discretionary Select Sector SPDR Fund)
* amc = AMC Theatres
* cnk = Cinemark Theatres
* msgs = Madison Square Garden Sports Corp
* seas = Seaworld Entertainment Inc
* wwe = World Wrestling Entertainment Inc

In [2]:
ent_stocks = data.DataReader(['amc', 'cnk', 'msgs','seas', 'wwe', 'xly'],start='2019-08-16',end=end_date,data_source='yahoo') ['Adj Close']
ent_stock_df_plot = ent_stocks.hvplot(title="Entertainment Industry Closing Price", shared_axes=False)
ent_stocks_pct_change=ent_stocks.pct_change()
ent_stocks_daily_returns_df_plot = ent_stocks_pct_change.hvplot(title="Entertainment Industry Pct.Change", shared_axes=False)
ent_cumulative_returns=(1+ent_stocks_pct_change).cumprod()-1
ent_cum_returns_df_plot = ent_cumulative_returns.hvplot(title="Entertainment Cumulative Returns")
ent_sharpe_ratios=(ent_stocks_pct_change.mean()*252)/(ent_stocks_pct_change.std()*np.sqrt(252))
ent_sharpe_ratios.sort_values(inplace=True)
ent_sharpe_ratios_plot = ent_sharpe_ratios.hvplot.bar(shared_axes=False)
ent_daily_std=ent_stocks_pct_change.std()
risky_ent=ent_daily_std[ent_daily_std>ent_daily_std["xly"]]
annualized_ent_std=ent_daily_std*np.sqrt(252)
ent_rolling_window = ent_stocks_pct_change.rolling(window=30).mean().hvplot(shared_axes=False)
amc_rolling = ent_stocks["amc"].rolling(window=30).std().hvplot(shared_axes=False)
cnk_rolling = ent_stocks["cnk"].rolling(window=30).std().hvplot(shared_axes=False)
msgs_rolling = ent_stocks["msgs"].rolling(window=30).std().hvplot(shared_axes=False)
seas_rolling = ent_stocks["seas"].rolling(window=30).std().hvplot(shared_axes=False)
wwe_rolling = ent_stocks["wwe"].rolling(window=30).std().hvplot(shared_axes=False)
ent_combined_rolling_plot = amc_rolling*cnk_rolling*msgs_rolling*seas_rolling*wwe_rolling

### RESTAURANTS
* mcd = McDonald's Corporation
* sbux = Starbucks Corporation
* yum = Yum Brands Inc
* txrh = Texas Roadhouse Inc
* cbrl = Cracker Barrel Old Country Store

In [3]:
res_stocks = data.DataReader(['mcd', 'sbux', 'yum','txrh', 'cbrl', 'xly'],start='2019-08-01',end=end_date,data_source='yahoo') ['Adj Close']
res_stock_df_plot = res_stocks.hvplot(title="Restaurant Industry Closing Price", shared_axes=False)
res_stocks_pct_change=res_stocks.pct_change()
res_stock_daily_returns_plot = res_stocks_pct_change.hvplot(title="Restaurant Industry Pct.Change", shared_axes=False)
res_cumulative_returns=(1+res_stocks_pct_change).cumprod()-1
res_cum_returns_df_plot = res_cumulative_returns.hvplot(title="Restaurant Cumulative Returns", shared_axes=False)
res_sharpe_ratios=(res_stocks_pct_change.mean()*252)/(res_stocks_pct_change.std()*np.sqrt(252))
res_sharpe_ratios.sort_values(inplace=True)
res_sharpe_ratios_plot = res_sharpe_ratios.hvplot.bar(shared_axes=False)
res_daily_std=res_stocks_pct_change.std()
risky_res=res_daily_std[res_daily_std>res_daily_std["xly"]]
annualized_res_std=res_daily_std*np.sqrt(252)
res_rolling_window = res_stocks_pct_change.rolling(window=30).mean().hvplot(title= 'Restaurant Sector 30 Day Moving Average',shared_axes=False)

### HOTELS
* mar = Marriott International Inc
* hlt = Hilton Worldwide Holdings Inc
* rcl = Royal Caribbean Group 
* h = Hyatt Hotels Corp
* chh = Choice Hotels International Inc


In [4]:
hot_stocks = data.DataReader(['mar', 'hlt', 'rcl','h', 'chh','xly'],start='2019-08-01',end=end_date,data_source='yahoo') ['Adj Close']
hot_stocks_df_plot = hot_stocks.hvplot(title="Hotel/Resorts/Cruises Industry Closing Price")
hot_stocks_pct_change=hot_stocks.pct_change()
hot_stocks_daily_returns_plot = hot_stocks_pct_change.hvplot(title="Hotel Industry Pct.Change",shared_axes=False)
hot_cumulative_returns=(1+hot_stocks_pct_change).cumprod()-1
hot_cum_returns_df_plot = hot_cumulative_returns.hvplot(title = "Hotel Sector Cumulative Returns",shared_axes=False)
hot_sharpe_ratios=(hot_stocks_pct_change.mean()*252)/(hot_stocks_pct_change.std()*np.sqrt(252))
hot_sharpe_ratios.sort_values(inplace=True)
hot_sharpe_ratio_plot = hot_sharpe_ratios.hvplot.bar(shared_axes=False)
hot_daily_std=hot_stocks_pct_change.std()
risky_hot=hot_daily_std[hot_daily_std>hot_daily_std["xly"]]
annualized_hot_std=hot_daily_std*np.sqrt(252)
hot_rolling_window = hot_stocks_pct_change.rolling(window=30).mean().hvplot(title= "Hotel Sector 30 Day Moving Average", shared_axes=False)

## MONTE CARLO SIMULATIONS -- ENTERTAINMENT

In [5]:
avg_daily_return_amc = ent_stocks_pct_change.mean()['amc']
avg_daily_return_cnk = ent_stocks_pct_change.mean()['cnk']
avg_daily_return_msgs = ent_stocks_pct_change.mean()['msgs']
avg_daily_return_seas = ent_stocks_pct_change.mean()['seas']
avg_daily_return_wwe = ent_stocks_pct_change.mean()['wwe']
avg_daily_return_xly = ent_stocks_pct_change.mean()['xly']
std_dev_daily_return_amc = ent_stocks_pct_change.std()['amc']
std_dev_daily_return_cnk = ent_stocks_pct_change.std()['cnk']
std_dev_daily_return_msgs = ent_stocks_pct_change.std()['msgs']
std_dev_daily_return_seas = ent_stocks_pct_change.std()['seas']
std_dev_daily_return_wwe = ent_stocks_pct_change.std()['wwe']
std_dev_daily_return_xly = ent_stocks_pct_change.std()['xly']
amc_last_price = ent_stocks['amc'][-1]
cnk_last_price = ent_stocks['cnk'][-1]
msgs_last_price = ent_stocks['msgs'][-1]
seas_last_price = ent_stocks['seas'][-1]
wwe_last_price = ent_stocks['wwe'][-1]
xly_last_price = ent_stocks['xly'][-1]
number_simulations = 1000
number_records = 252
monte_carlo = pd.DataFrame()
simulated_amc_prices = [amc_last_price]
simulated_cnk_prices = [cnk_last_price]
simulated_msgs_prices = [msgs_last_price]
simulated_seas_prices = [seas_last_price]
simulated_wwe_prices = [wwe_last_price]
simulated_xly_prices = [xly_last_price]
ent_simulated_price_df = pd.DataFrame()
ent_portfolio_cumulative_returns = pd.DataFrame()
for n in range(number_simulations):
    simulated_amc_prices = [amc_last_price]
    simulated_cnk_prices = [cnk_last_price]
    simulated_msgs_prices = [msgs_last_price]
    simulated_seas_prices = [seas_last_price]
    simulated_wwe_prices = [wwe_last_price]
    simulated_xly_prices = [xly_last_price]
    for i in range(number_records):
        simulated_amc_price = simulated_amc_prices[-1] * (1 + np.random.normal(avg_daily_return_amc, std_dev_daily_return_amc))
        simulated_cnk_price = simulated_cnk_prices[-1] * (1 + np.random.normal(avg_daily_return_cnk, std_dev_daily_return_cnk))
        simulated_msgs_price = simulated_msgs_prices[-1] * (1 + np.random.normal(avg_daily_return_msgs, std_dev_daily_return_msgs))
        simulated_seas_price = simulated_seas_prices[-1] * (1 + np.random.normal(avg_daily_return_seas, std_dev_daily_return_seas))
        simulated_wwe_price = simulated_wwe_prices[-1] * (1 + np.random.normal(avg_daily_return_wwe, std_dev_daily_return_wwe))
        simulated_xly_price = simulated_xly_prices[-1] * (1 + np.random.normal(avg_daily_return_xly, std_dev_daily_return_xly))
        simulated_amc_prices.append(simulated_amc_price)
        simulated_cnk_prices.append(simulated_cnk_price)
        simulated_msgs_prices.append(simulated_msgs_price) 
        simulated_seas_prices.append(simulated_seas_price) 
        simulated_wwe_prices.append(simulated_wwe_price) 
        simulated_xly_prices.append(simulated_xly_price) 
    ent_simulated_price_df["AMC prices"] = pd.Series(simulated_amc_prices)
    ent_simulated_price_df["CNK prices"] = pd.Series(simulated_cnk_prices)
    ent_simulated_price_df["MSGS prices"] = pd.Series(simulated_msgs_prices)
    ent_simulated_price_df["SEAS prices"] = pd.Series(simulated_seas_prices)
    ent_simulated_price_df["WWE prices"] = pd.Series(simulated_wwe_prices)
    ent_simulated_price_df["XLY prices"] = pd.Series(simulated_xly_prices)
    ent_simulated_daily_returns = ent_simulated_price_df.pct_change()         
ent_simulated_daily_returns_plot = ent_simulated_daily_returns.hvplot(title = "Entertainment Sector Simulated Daily Returns",shared_axes=False)
ent_simulated_price_df_plot = ent_simulated_price_df.hvplot(title= "Entertainment Sector Simulated Price",shared_axes=False)
              

## MONTE CARLO SIMULATIONS -- RESTAURANT

In [6]:
avg_daily_return_mcd = res_stocks_pct_change.mean()['mcd']
avg_daily_return_sbux = res_stocks_pct_change.mean()['sbux']
avg_daily_return_yum = res_stocks_pct_change.mean()['yum']
avg_daily_return_txrh = res_stocks_pct_change.mean()['txrh']
avg_daily_return_cbrl = res_stocks_pct_change.mean()['cbrl']
avg_daily_return_xly = res_stocks_pct_change.mean()['xly']
std_dev_daily_return_mcd = res_stocks_pct_change.std()['mcd']
std_dev_daily_return_sbux = res_stocks_pct_change.std()['sbux']
std_dev_daily_return_yum = res_stocks_pct_change.std()['yum']
std_dev_daily_return_txrh = res_stocks_pct_change.std()['txrh']
std_dev_daily_return_cbrl = res_stocks_pct_change.std()['cbrl']
std_dev_daily_return_xly = res_stocks_pct_change.std()['xly']
mcd_last_price = res_stocks['mcd'][-1]
sbux_last_price = res_stocks['sbux'][-1]
yum_last_price = res_stocks['yum'][-1]
txrh_last_price = res_stocks['txrh'][-1]
cbrl_last_price = res_stocks['cbrl'][-1]
xly_last_price = res_stocks['xly'][-1]
number_simulations = 1000
number_records = 252
monte_carlo2 = pd.DataFrame()
simulated_mcd_prices = [mcd_last_price]
simulated_sbux_prices = [sbux_last_price]
simulated_yum_prices = [yum_last_price]
simulated_txrh_prices = [txrh_last_price]
simulated_cbrl_prices = [cbrl_last_price]
simulated_xly_prices = [xly_last_price]
res_simulated_price_df = pd.DataFrame()
res_portfolio_cumulative_returns = pd.DataFrame()
for n in range(number_simulations):
    simulated_mcd_prices = [mcd_last_price]
    simulated_sbux_prices = [sbux_last_price]
    simulated_yum_prices = [yum_last_price]
    simulated_txrh_prices = [txrh_last_price]
    simulated_cbrl_prices = [cbrl_last_price]
    simulated_xly_prices = [xly_last_price]
    for i in range(number_records):
            simulated_mcd_price = simulated_mcd_prices[-1] * (1 + np.random.normal(avg_daily_return_mcd, std_dev_daily_return_mcd))
            simulated_sbux_price = simulated_sbux_prices[-1] * (1 + np.random.normal(avg_daily_return_sbux, std_dev_daily_return_sbux))
            simulated_yum_price = simulated_yum_prices[-1] * (1 + np.random.normal(avg_daily_return_yum, std_dev_daily_return_yum))
            simulated_txrh_price = simulated_txrh_prices[-1] * (1 + np.random.normal(avg_daily_return_txrh, std_dev_daily_return_txrh))
            simulated_cbrl_price = simulated_cbrl_prices[-1] * (1 + np.random.normal(avg_daily_return_cbrl, std_dev_daily_return_cbrl))
            simulated_xly_price = simulated_xly_prices[-1] * (1 + np.random.normal(avg_daily_return_xly, std_dev_daily_return_xly))
            simulated_mcd_prices.append(simulated_mcd_price)
            simulated_sbux_prices.append(simulated_sbux_price)
            simulated_yum_prices.append(simulated_yum_price) 
            simulated_txrh_prices.append(simulated_txrh_price) 
            simulated_cbrl_prices.append(simulated_cbrl_price) 
            simulated_xly_prices.append(simulated_xly_price)  
    res_simulated_price_df["MCD prices"] = pd.Series(simulated_mcd_prices)
    res_simulated_price_df["SBUX prices"] = pd.Series(simulated_sbux_prices)
    res_simulated_price_df["YUM prices"] = pd.Series(simulated_yum_prices)
    res_simulated_price_df["TXRH prices"] = pd.Series(simulated_txrh_prices)
    res_simulated_price_df["CBRL prices"] = pd.Series(simulated_cbrl_prices)
    res_simulated_price_df["XLY prices"] = pd.Series(simulated_xly_prices)
    res_simulated_daily_returns = res_simulated_price_df.pct_change()       
res_simulated_daily_returns_plot = res_simulated_daily_returns.hvplot(title= "Restaurant Sector Simulated Daily Returns",shared_axes=False)
res_simulated_price_df_plot = res_simulated_price_df.hvplot(shared_axes=False)


## MONTE CARLO SIMULATIONS -- HOTELS

In [7]:
avg_daily_return_mar = hot_stocks_pct_change.mean()['mar']
avg_daily_return_hlt = hot_stocks_pct_change.mean()['hlt']
avg_daily_return_rcl = hot_stocks_pct_change.mean()['rcl']
avg_daily_return_h = hot_stocks_pct_change.mean()['h']
avg_daily_return_chh = hot_stocks_pct_change.mean()['chh']
avg_daily_return_xly = hot_stocks_pct_change.mean()['xly']
std_dev_daily_return_mar = hot_stocks_pct_change.std()['mar']
std_dev_daily_return_hlt = hot_stocks_pct_change.std()['hlt']
std_dev_daily_return_rcl = hot_stocks_pct_change.std()['rcl']
std_dev_daily_return_h = hot_stocks_pct_change.std()['h']
std_dev_daily_return_chh = hot_stocks_pct_change.std()['chh']
std_dev_daily_return_xly = hot_stocks_pct_change.std()['xly']
mar_last_price = hot_stocks['mar'][-1]
hlt_last_price = hot_stocks['hlt'][-1]
rcl_last_price = hot_stocks['rcl'][-1]
h_last_price = hot_stocks['h'][-1]
chh_last_price = hot_stocks['chh'][-1]
xly_last_price = hot_stocks['xly'][-1]
number_simulations = 1000
number_records = 252
monte_carlo3 = pd.DataFrame()
simulated_mar_prices = [mar_last_price]
simulated_hlt_prices = [hlt_last_price]
simulated_rcl_prices = [rcl_last_price]
simulated_h_prices = [h_last_price]
simulated_chh_prices = [chh_last_price]
simulated_xly_prices = [xly_last_price]
hot_simulated_price_df = pd.DataFrame()
hot_portfolio_cumulative_returns = pd.DataFrame()
for n in range(number_simulations):
    simulated_mar_prices = [mar_last_price]
    simulated_hlt_prices = [hlt_last_price]
    simulated_rcl_prices = [rcl_last_price]
    simulated_h_prices = [h_last_price]
    simulated_chh_prices = [chh_last_price]
    simulated_xly_prices = [xly_last_price]
    for i in range(number_records):
        simulated_mar_price = simulated_mar_prices[-1] * (1 + np.random.normal(avg_daily_return_mar, std_dev_daily_return_mar))
        simulated_hlt_price = simulated_hlt_prices[-1] * (1 + np.random.normal(avg_daily_return_hlt, std_dev_daily_return_hlt))
        simulated_rcl_price = simulated_rcl_prices[-1] * (1 + np.random.normal(avg_daily_return_rcl, std_dev_daily_return_rcl))
        simulated_h_price = simulated_h_prices[-1] * (1 + np.random.normal(avg_daily_return_h, std_dev_daily_return_h))
        simulated_chh_price = simulated_chh_prices[-1] * (1 + np.random.normal(avg_daily_return_chh, std_dev_daily_return_chh))
        simulated_xly_price = simulated_xly_prices[-1] * (1 + np.random.normal(avg_daily_return_xly, std_dev_daily_return_xly))
        simulated_mar_prices.append(simulated_mar_price)
        simulated_hlt_prices.append(simulated_hlt_price)
        simulated_rcl_prices.append(simulated_rcl_price) 
        simulated_h_prices.append(simulated_h_price) 
        simulated_chh_prices.append(simulated_chh_price) 
        simulated_xly_prices.append(simulated_xly_price) 
    hot_simulated_price_df["MAR prices"] = pd.Series(simulated_mar_prices)
    hot_simulated_price_df["HLT prices"] = pd.Series(simulated_hlt_prices)
    hot_simulated_price_df["RCL prices"] = pd.Series(simulated_yum_prices)
    hot_simulated_price_df["H prices"] = pd.Series(simulated_h_prices)
    hot_simulated_price_df["CHH prices"] = pd.Series(simulated_chh_prices)
    hot_simulated_price_df["XLY prices"] = pd.Series(simulated_xly_prices)
    hot_simulated_daily_returns = hot_simulated_price_df.pct_change()
hot_simulated_daily_returns_plot = hot_simulated_daily_returns.hvplot(shared_axes=False)    
hot_simulated_price_df_plot = hot_simulated_price_df.hvplot(shared_axes=False)        
   
    
 

In [8]:
# Calculate Beta for a single stock compared to etf
ent_rolling_covariance = ent_stocks_pct_change['cnk'].rolling(window=30).cov(ent_stocks_pct_change['xly'])
ent_rolling_variance = ent_stocks_pct_change['cnk'].rolling(window=30).var()
ent_rolling_beta =ent_rolling_covariance/ent_rolling_variance
# ent_rolling_beta
ent_rolling_beta_plot = ent_rolling_beta.hvplot(title= '30 Day Rolling Beta of CNK vs XLY', shared_axes=False)

In [9]:
tab1 = pn.Column(ent_stock_df_plot)
tab2 = pn.Column(ent_stocks_daily_returns_df_plot)
tab3 = pn.Column(ent_cum_returns_df_plot)
tab4 = pn.Column(ent_rolling_window)
tab5 = pn.Column(ent_simulated_daily_returns_plot)
tab6 = pn.Column(ent_simulated_price_df_plot)
tab7 = pn.Column(ent_rolling_beta_plot)
Xavier = pn.Tabs(("Stock", tab1),
       ("Daily Returns", tab2),
       ("Cumulative Returns", tab3),
       ("30 Moving Average", tab4),
       ("Simulated Daily Returns", tab5),
       ("Simulated Price", tab6),
       ("Rolling Beta", tab7))

# ----------------------------------------------------

# Richards work

In [10]:
tech_stocks = data.DataReader(["AAPL", "GOOG", "AMZN", "TSLA", "NFLX", "QQQ"],start='2019-08-16', end=end_date, data_source='yahoo')['Adj Close']
tech_stock_price_plot = tech_stocks.hvplot(title="Tech Stock Prices Over the Last Year", shared_axes=False)
crypto = data.DataReader(["BTC-USD", "ETH-USD", "XRP-USD", "LINK-USD", "LTC-USD"],start='2019-08-16', end=end_date, data_source='yahoo')['Adj Close']
crypto_price_plot = crypto.hvplot(title = "Crypto Price Over The Last Year", shared_axes=False)
tech_stocks_daily_returns = tech_stocks.pct_change()
tech_stocks_daily_returns.dropna(inplace=True)
tech_stocks_daily_returns_plot = tech_stocks_daily_returns.hvplot(title="Tech Stocks Daily Returns", shared_axes=False)
crypto_daily_returns = crypto.pct_change()
crypto_daily_returns.dropna(inplace=True)
crypto_daily_returns_plot = crypto_daily_returns.hvplot(title="Crypto Daily Returns", shared_axes=False)
cumulative_returns_tech = (1 + tech_stocks_daily_returns).cumprod() -1
tech_stock_cum_returns_plot = cumulative_returns_tech.hvplot(title = "Tech Stocks Cumulative Returns", shared_axes=False)
cumulative_returns_crypto = (1 + crypto_daily_returns).cumprod() -1
crypto_cum_returns_plot = cumulative_returns_crypto.hvplot(title = "Crypto Cumulative Returns", shared_axes=False)
tech_stocks_std = tech_stocks_daily_returns.std()
tech_stocks_std = tech_stocks_std.sort_values(ascending = False)
riskier_tech = tech_stocks_std[tech_stocks_std>tech_stocks_std['QQQ']]
tech_stocks_std = tech_stocks_daily_returns.std()
tech_stocks_std = tech_stocks_std.sort_values(ascending = False)
aapl_rolling_std = tech_stocks_daily_returns['AAPL'].rolling(window=30).std().hvplot(title = "Tech Stocks 30 Day Rolling STD", shared_axes=False)
goog_rolling_std = tech_stocks_daily_returns['GOOG'].rolling(window=30).std().hvplot(shared_axes=False)
amzn_rolling_std = tech_stocks_daily_returns['AMZN'].rolling(window=30).std().hvplot(shared_axes=False)
tsla_rolling_std = tech_stocks_daily_returns['TSLA'].rolling(window=30).std().hvplot(shared_axes=False)
nflx_rolling_std = tech_stocks_daily_returns['NFLX'].rolling(window=30).std().hvplot(shared_axes=False)
qqq_rolling_std = tech_stocks_daily_returns['QQQ'].rolling(window=30).std().hvplot(shared_axes=False)
rolling_tech_plot = aapl_rolling_std*goog_rolling_std*amzn_rolling_std*tsla_rolling_std*nflx_rolling_std*qqq_rolling_std
btc_rolling_std = crypto_daily_returns['BTC-USD'].rolling(window=30).std().hvplot(title = "Crypto 30 Day Rolling STD", shared_axes=False)
eth_rolling_std = crypto_daily_returns['ETH-USD'].rolling(window=30).std().hvplot(shared_axes=False)
link_rolling_std = crypto_daily_returns['LINK-USD'].rolling(window=30).std().hvplot(shared_axes=False)
ltc_rolling_std = crypto_daily_returns['LTC-USD'].rolling(window=30).std().hvplot(shared_axes=False)
xrp_rolling_std = crypto_daily_returns['XRP-USD'].rolling(window=30).std().hvplot(shared_axes=False)
crypto_rolling_plot = btc_rolling_std*eth_rolling_std*link_rolling_std*ltc_rolling_std*xrp_rolling_std
correlation_tech = tech_stocks_daily_returns.corr()
correlation_crypto = crypto_daily_returns.corr()
tech_rolling_covariance = tech_stocks_daily_returns['TSLA'].rolling(window=30).cov(tech_stocks_daily_returns['QQQ'])
tech_rolling_variance = tech_stocks_daily_returns['TSLA'].rolling(window=30).var()
tech_rolling_beta = tech_rolling_covariance / tech_rolling_variance
tech_rolling_beta_plot = tech_rolling_beta.hvplot(title = '30 Day Rolling Beta of Tesla vs. QQQ', shared_axes=False)
tech_daily_returns_ewm = tech_stocks_daily_returns.ewm(halflife=30).std()
tech_stock_ewm_plot = tech_daily_returns_ewm.hvplot(title = 'Tech Stocks 30 Day EWM', shared_axes=False)
crypto_daily_returns_ewm = crypto_daily_returns.ewm(halflife=30).std()
crypto_ewm_plot = crypto_daily_returns_ewm.hvplot(title = 'Crypto 30 Day EWM', shared_axes=False)
tech_sharpe_ratios = (tech_stocks_daily_returns.mean() * 252) / (tech_stocks_daily_returns.std() * np.sqrt(252))
tech_sharpe_plot = tech_sharpe_ratios.hvplot.bar(title = "Tech Stock Sharpe Ratios", shared_axes=False)
crypto_sharpe_ratios = (crypto_daily_returns.mean() * 252) / (crypto_daily_returns.std() * np.sqrt(252))
crypto_sharpe_plot = crypto_sharpe_ratios.hvplot.bar(title = "Crypto Sharpe Ratios", shared_axes=False)


### Run the monte carlo simulation for tech stocks

In [11]:
# -------Tech stocks for the next year------

avg_daily_return_aapl = tech_stocks_daily_returns.mean()['AAPL']
avg_daily_return_goog = tech_stocks_daily_returns.mean()['GOOG']
avg_daily_return_tsla = tech_stocks_daily_returns.mean()['TSLA']
avg_daily_return_nflx = tech_stocks_daily_returns.mean()['NFLX']
avg_daily_return_amzn = tech_stocks_daily_returns.mean()['AMZN']
avg_daily_return_qqq = tech_stocks_daily_returns.mean()['QQQ']
std_dev_daily_return_aapl = tech_stocks_daily_returns.std()['AAPL']
std_dev_daily_return_goog = tech_stocks_daily_returns.std()['GOOG']
std_dev_daily_return_tsla = tech_stocks_daily_returns.std()['TSLA']
std_dev_daily_return_nflx = tech_stocks_daily_returns.std()['NFLX']
std_dev_daily_return_amzn = tech_stocks_daily_returns.std()['AMZN']
std_dev_daily_return_qqq = tech_stocks_daily_returns.std()['QQQ']
aapl_last_price = tech_stocks['AAPL'][-1]
goog_last_price = tech_stocks['GOOG'][-1]
tsla_last_price = tech_stocks['TSLA'][-1]
nflx_last_price = tech_stocks['NFLX'][-1]
amzn_last_price = tech_stocks['AMZN'][-1]
qqq_last_price = tech_stocks['QQQ'][-1]
number_simulations = 1000
number_records = 252
monte_carlo = pd.DataFrame()
simulated_aapl_prices = [aapl_last_price]
simulated_goog_prices = [goog_last_price]
simulated_tsla_prices = [tsla_last_price]
simulated_nflx_prices = [nflx_last_price]
simulated_amzn_prices = [amzn_last_price]
simulated_qqq_prices = [qqq_last_price]
simulated_price_df = pd.DataFrame()
tech_portfolio_cumulative_returns = pd.DataFrame()
for n in range(number_simulations):
    simulated_aapl_prices = [aapl_last_price]
    simulated_goog_prices = [goog_last_price]
    simulated_tsla_prices = [tsla_last_price]
    simulated_nflx_prices = [nflx_last_price]
    simulated_amzn_prices = [amzn_last_price]
    simulated_qqq_prices = [qqq_last_price]
    for i in range(number_records):
        simulated_aapl_price = simulated_aapl_prices[-1] * (1 + np.random.normal(avg_daily_return_aapl, std_dev_daily_return_aapl))
        simulated_goog_price = simulated_goog_prices[-1] * (1 + np.random.normal(avg_daily_return_goog, std_dev_daily_return_goog))
        simulated_tsla_price = simulated_tsla_prices[-1] * (1 + np.random.normal(avg_daily_return_tsla, std_dev_daily_return_tsla))
        simulated_nflx_price = simulated_nflx_prices[-1] * (1 + np.random.normal(avg_daily_return_nflx, std_dev_daily_return_nflx))
        simulated_amzn_price = simulated_amzn_prices[-1] * (1 + np.random.normal(avg_daily_return_amzn, std_dev_daily_return_amzn))
        simulated_qqq_price = simulated_qqq_prices[-1] * (1 + np.random.normal(avg_daily_return_qqq, std_dev_daily_return_qqq)) 
        simulated_aapl_prices.append(simulated_aapl_price)
        simulated_goog_prices.append(simulated_goog_price)
        simulated_tsla_prices.append(simulated_tsla_price) 
        simulated_nflx_prices.append(simulated_nflx_price) 
        simulated_amzn_prices.append(simulated_amzn_price) 
        simulated_qqq_prices.append(simulated_qqq_price) 
    simulated_price_df["AAPL prices"] = pd.Series(simulated_aapl_prices)
    simulated_price_df["GOOG prices"] = pd.Series(simulated_goog_prices)
    simulated_price_df["TSLA prices"] = pd.Series(simulated_tsla_prices)
    simulated_price_df["NFLX prices"] = pd.Series(simulated_nflx_prices)
    simulated_price_df["AMZN prices"] = pd.Series(simulated_amzn_prices)
    simulated_price_df["QQQ prices"] = pd.Series(simulated_qqq_prices)
    simulated_daily_returns = simulated_price_df.pct_change()
simulated_tech_returns = simulated_daily_returns.hvplot(title="Tech stocks simulated daily returns for the next year", shared_axes=False)
simulated_tech_price = simulated_price_df.hvplot(title="Tech Stocks future price thru the next year", shared_axes=False)

In [12]:
#------- Crypto for the next year---------

avg_daily_return_btc = crypto_daily_returns.mean()['BTC-USD']
avg_daily_return_eth = crypto_daily_returns.mean()['ETH-USD']
avg_daily_return_ltc = crypto_daily_returns.mean()['LTC-USD']
avg_daily_return_link = crypto_daily_returns.mean()['LINK-USD']
avg_daily_return_xrp = crypto_daily_returns.mean()['XRP-USD']
std_dev_daily_return_btc = crypto_daily_returns.std()['BTC-USD']
std_dev_daily_return_eth = crypto_daily_returns.std()['ETH-USD']
std_dev_daily_return_ltc = crypto_daily_returns.std()['LTC-USD']
std_dev_daily_return_link = crypto_daily_returns.std()['LINK-USD']
std_dev_daily_return_xrp = crypto_daily_returns.std()['XRP-USD']
btc_last_price = crypto['BTC-USD'][-1]
eth_last_price = crypto['ETH-USD'][-1]
ltc_last_price = crypto['LTC-USD'][-1]
link_last_price = crypto['LINK-USD'][-1]
xrp_last_price = crypto['XRP-USD'][-1]
number_simulations2 = 1000
number_records2 = 252
monte_carlo2 = pd.DataFrame()
simulated_btc_prices = [btc_last_price]
simulated_eth_prices = [eth_last_price]
simulated_ltc_prices = [ltc_last_price]
simulated_link_prices = [link_last_price]
simulated_xrp_prices = [xrp_last_price]
simulated_price_df2 = pd.DataFrame()
crypto_portfolio_cumulative_returns = pd.DataFrame()
for n in range(number_simulations2):  
    simulated_btc_prices = [btc_last_price]
    simulated_eth_prices = [eth_last_price]
    simulated_ltc_prices = [ltc_last_price]
    simulated_link_prices = [link_last_price]
    simulated_xrp_prices = [xrp_last_price]
    for i in range(number_records):    
        simulated_btc_price = simulated_btc_prices[-1] * (1 + np.random.normal(avg_daily_return_btc, std_dev_daily_return_btc))
        simulated_eth_price = simulated_eth_prices[-1] * (1 + np.random.normal(avg_daily_return_eth, std_dev_daily_return_eth))
        simulated_ltc_price = simulated_ltc_prices[-1] * (1 + np.random.normal(avg_daily_return_ltc, std_dev_daily_return_ltc))
        simulated_link_price = simulated_link_prices[-1] * (1 + np.random.normal(avg_daily_return_link, std_dev_daily_return_link))
        simulated_xrp_price = simulated_xrp_prices[-1] * (1 + np.random.normal(avg_daily_return_xrp, std_dev_daily_return_xrp))
        simulated_btc_prices.append(simulated_btc_price)
        simulated_eth_prices.append(simulated_eth_price)
        simulated_ltc_prices.append(simulated_ltc_price) 
        simulated_link_prices.append(simulated_link_price) 
        simulated_xrp_prices.append(simulated_xrp_price)  
    simulated_price_df2["BTC prices"] = pd.Series(simulated_btc_prices)
    simulated_price_df2["ETH prices"] = pd.Series(simulated_eth_prices)
    simulated_price_df2["LTC prices"] = pd.Series(simulated_ltc_prices)
    simulated_price_df2["LINK prices"] = pd.Series(simulated_link_prices)
    simulated_price_df2["XRP prices"] = pd.Series(simulated_xrp_prices)
    simulated_daily_returns2 = simulated_price_df2.pct_change()
simulated_crypto_daily_returns = simulated_daily_returns2.hvplot(shared_axes=False, title = "Crypto Simulated Daily Returns")
simulated_crypto_prices = simulated_price_df2.hvplot(shared_axes=False, title="Crypto Simulated Future Price")


In [13]:
#------- Tech stocks up to 2020-05-31  --------------------

tech_stocks3 = data.DataReader(["AAPL", "GOOG", "AMZN", "TSLA", "NFLX", "QQQ"],start='2019-08-16', end= '2020-05-31', data_source='yahoo')['Adj Close']
tech_stocks_daily_returns3 = tech_stocks3.pct_change()
avg_daily_return_aapl3 = tech_stocks_daily_returns3.mean()['AAPL']
avg_daily_return_goog3 = tech_stocks_daily_returns3.mean()['GOOG']
avg_daily_return_tsla3 = tech_stocks_daily_returns3.mean()['TSLA']
avg_daily_return_nflx3 = tech_stocks_daily_returns3.mean()['NFLX']
avg_daily_return_amzn3 = tech_stocks_daily_returns3.mean()['AMZN']
avg_daily_return_qqq3 = tech_stocks_daily_returns3.mean()['QQQ']
std_dev_daily_return_aapl3 = tech_stocks_daily_returns3.std()['AAPL']
std_dev_daily_return_goog3 = tech_stocks_daily_returns3.std()['GOOG']
std_dev_daily_return_tsla3 = tech_stocks_daily_returns3.std()['TSLA']
std_dev_daily_return_nflx3 = tech_stocks_daily_returns3.std()['NFLX']
std_dev_daily_return_amzn3 = tech_stocks_daily_returns3.std()['AMZN']
std_dev_daily_return_qqq3 = tech_stocks_daily_returns3.std()['QQQ']
aapl_last_price3 = tech_stocks3['AAPL'][-1]
goog_last_price3 = tech_stocks3['GOOG'][-1]
tsla_last_price3 = tech_stocks3['TSLA'][-1]
nflx_last_price3 = tech_stocks3['NFLX'][-1]
amzn_last_price3 = tech_stocks3['AMZN'][-1]
qqq_last_price3 = tech_stocks3['QQQ'][-1]
number_simulations3 = 1000
number_records3 = 45
monte_carlo3 = pd.DataFrame()
simulated_aapl_prices3 = [aapl_last_price3]
simulated_goog_prices3 = [goog_last_price3]
simulated_tsla_prices3 = [tsla_last_price3]
simulated_nflx_prices3 = [nflx_last_price3]
simulated_amzn_prices3 = [amzn_last_price3]
simulated_qqq_prices3 = [qqq_last_price3]
simulated_price_df3 = pd.DataFrame()
tech_portfolio_cumulative_returns3 = pd.DataFrame()
for n in range(number_simulations3):
    simulated_aapl_prices3 = [aapl_last_price3]
    simulated_goog_prices3 = [goog_last_price3]
    simulated_tsla_prices3 = [tsla_last_price3]
    simulated_nflx_prices3 = [nflx_last_price3]
    simulated_amzn_prices3 = [amzn_last_price3]
    simulated_qqq_prices3 = [qqq_last_price3]
    for i in range(number_records3):
        simulated_aapl_price3 = simulated_aapl_prices3[-1] * (1 + np.random.normal(avg_daily_return_aapl3, std_dev_daily_return_aapl3))
        simulated_goog_price3 = simulated_goog_prices3[-1] * (1 + np.random.normal(avg_daily_return_goog3, std_dev_daily_return_goog3))
        simulated_tsla_price3 = simulated_tsla_prices3[-1] * (1 + np.random.normal(avg_daily_return_tsla3, std_dev_daily_return_tsla3))
        simulated_nflx_price3 = simulated_nflx_prices3[-1] * (1 + np.random.normal(avg_daily_return_nflx3, std_dev_daily_return_nflx3))
        simulated_amzn_price3 = simulated_amzn_prices3[-1] * (1 + np.random.normal(avg_daily_return_amzn3, std_dev_daily_return_amzn3))
        simulated_qqq_price3 = simulated_qqq_prices3[-1] * (1 + np.random.normal(avg_daily_return_qqq3, std_dev_daily_return_qqq3))
        simulated_aapl_prices3.append(simulated_aapl_price3)
        simulated_goog_prices3.append(simulated_goog_price3)
        simulated_tsla_prices3.append(simulated_tsla_price3) 
        simulated_nflx_prices3.append(simulated_nflx_price3) 
        simulated_amzn_prices3.append(simulated_amzn_price3) 
        simulated_qqq_prices3.append(simulated_qqq_price3) 
    simulated_price_df3["AAPL prices"] = pd.Series(simulated_aapl_prices3)
    simulated_price_df3["GOOG prices"] = pd.Series(simulated_goog_prices3)
    simulated_price_df3["TSLA prices"] = pd.Series(simulated_tsla_prices3)
    simulated_price_df3["NFLX prices"] = pd.Series(simulated_nflx_prices3)
    simulated_price_df3["AMZN prices"] = pd.Series(simulated_amzn_prices3)
    simulated_price_df3["QQQ prices"] = pd.Series(simulated_qqq_prices3)
    simulated_daily_returns3 = simulated_price_df3.pct_change()
simulated_comparison_plot = simulated_price_df3.hvplot(title = "Simulated Tech Stocks June - July 2020", shared_axes=False)


In [14]:
tech_stocks4 = data.DataReader(["AAPL", "GOOG", "AMZN", "TSLA", "NFLX", "QQQ"],start='2020-06-01', end= '2020-07-31', data_source='yahoo')['Adj Close']
actual_tech_stock_comparison = tech_stocks4.hvplot(title = "Actual Tech Stock Prices for June - July 2020", shared_axes=False)
combined_comparison_plot = actual_tech_stock_comparison + simulated_comparison_plot
combined_comparison_plot = combined_comparison_plot.opts(title = " Actual Tech Stock Prices in June - July 2020 Vs. The Monte Carlo Simulated Prices", shared_axes=False)

In [15]:
row1 = pn.Row(tech_stock_price_plot, crypto_price_plot)
row2 = pn.Row(tech_stocks_daily_returns_plot, crypto_daily_returns_plot)
row3 = pn.Row(rolling_tech_plot, crypto_rolling_plot)
row4 = pn.Row(tech_stock_cum_returns_plot, crypto_cum_returns_plot)
row5 = pn.Row(actual_tech_stock_comparison, simulated_comparison_plot)
row6 = pn.Row(simulated_tech_returns, simulated_tech_price)
row7 = pn.Row(simulated_crypto_daily_returns, simulated_crypto_prices)
row8 = pn.Row(simulated_comparison_plot, actual_tech_stock_comparison)
Tab1 = pn.Column(row1, row2)
Tab2 = pn.Column(tech_rolling_beta_plot, row3, row4)
Tab3 = pn.Column(tech_stock_ewm_plot, crypto_ewm_plot)
Tab4 = pn.Column(row6, row7, row8)
Richard = pn.Tabs(("Prices and Percent Change", Tab1),
        ("Rolling Plots and Cum Returns", Tab2),
        ("Exponentially Weighted Moving Avg", Tab3),
        ("Monte Carlo Simulations", Tab4))

# ------------------------------------------------------------------------------------------------

# Sheldon's work

In [16]:
Health_care_df = data.DataReader(["UNH","JNJ","MRK", "ABBV", "ABT","XLV"],start='2019-08-16',end=end_date,data_source='yahoo')['Adj Close']
health_care_df_plot = Health_care_df.hvplot(shared_axes=False,
                                            title="Health Care Data Over the Last Year",
                                            hover_color=["goldenrod"],
                                            hover_alpha=.6,
                                            grid=True,
                                            colorbar=True,
                                            hover=True,
                                            tools=["crosshair","pan"], 
                                            attr_labels=False, 
                                            height=350)
health_care_daily = Health_care_df.pct_change()
health_care_daily.dropna(inplace=True)
health_care_daily_plot = health_care_daily.hvplot(shared_axes=False,
                                                  title="Health Care Daily Percent Change Over the Last Year",
                                                  hover_color=["goldenrod"],
                                                  hover_alpha=.6,
                                                  grid=True,
                                                  colorbar=True,
                                                  hover=True,
                                                  tools=["crosshair","pan"], 
                                                  attr_labels=False, 
                                                  height=350)
health_cumprod_re = (1+health_care_daily).cumprod()-1
health_cumprod_re_plot = health_cumprod_re.hvplot(shared_axes=False,
                                                  alpha=1,
                                                  title="Health Care Cumulative Return",
                                                  hover_color=["goldenrod"],
                                                  hover_alpha=.6,
                                                  grid=True,
                                                  colorbar=True,
                                                  hover=True,
                                                  tools=["crosshair","pan"], 
                                                  attr_labels=False, 
                                                  height=350)
health_care_std = health_care_daily.std().sort_values(ascending=False)
health_risk = health_care_std[health_care_std>health_care_std["XLV"]]
health_rolling_window_plot = health_care_daily.rolling(window=30).std().hvplot(shared_axes=False,
                                                                               title="Health Care 30 Day Rolling Window",
                                                                               hover_color=["goldenrod"],
                                                                               hover_alpha=.6,
                                                                               grid=True,
                                                                               colorbar=True,
                                                                               hover=True,
                                                                               tools=["crosshair","pan"], 
                                                                               attr_labels=False, 
                                                                               height=350)
health_care_sharpe_ratio = (health_care_daily.mean()*252)/(health_care_daily.std()*np.sqrt(252))
health_care_sharpe_ratio_plot = health_care_sharpe_ratio.hvplot.bar(shared_axes=False,
                                                                    title="Health Care Sharp Ratio",
                                                                    hover_color=["goldenrod"],
                                                                    hover_alpha=.6,
                                                                    grid=True,
                                                                    colorbar=True,
                                                                    hover=True,
                                                                    tools=["crosshair","pan"], 
                                                                    attr_labels=False, 
                                                                    height=350)
health_care_daily_mean = health_care_daily.mean()
health_care_daily_std = health_care_daily.std()
health_daily_ewm_plot = health_care_daily.ewm(halflife=30).std().hvplot(shared_axes=False,
                                                                        title="Health Care Exponentially Weighted Moving Avg",
                                                                        hover_color=["goldenrod"],
                                                                        hover_alpha=.6,
                                                                        grid=True,
                                                                        colorbar=True,
                                                                        hover=True,
                                                                        tools=["crosshair","pan"], 
                                                                        attr_labels=False, 
                                                                        height=350)
JNJ_rolling_covariance = health_care_daily['JNJ'].rolling(window=30).cov(health_care_daily["XLV"])
JNJ_rolling_variance = health_care_daily['JNJ'].rolling(window=30).var()
JNJ_rolling_beta =JNJ_rolling_covariance/JNJ_rolling_variance
JNJ_rolling_beta_plot = JNJ_rolling_beta.hvplot(shared_axes=False,
                                                muted_alpha=True,
                                                title="Johnson & Johnson compared to Health Care SPDR",
                                                hover_color=["goldenrod"],
                                                hover_alpha=.6,
                                                grid=True,
                                                colorbar=True,
                                                hover=True,
                                                tools=["crosshair","pan"],
                                                attr_labels=False,
                                                height=350)

In [17]:
Communication_df = data.DataReader(["CMSA","BIDU","DISH", "TMUS", "ZM", "IXP"],start='2019-08-16',end=end_date,data_source='yahoo')['Adj Close']
comm_df_plot = Communication_df.hvplot(shared_axes=False,
                                       title="Communication Data Over the Last Year",
                                       hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                       hover_alpha=.6,
                                       grid=True,
                                       colorbar=True,
                                       hover=True,
                                       tools=["crosshair","pan"], 
                                       attr_labels=False, 
                                       height=350)
comm_daily= Communication_df.pct_change().dropna()
comm_daily_plot = comm_daily.hvplot(shared_axes=False,
                                    title="Communication Percent Change Over the Last Year",
                                    hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                    hover_alpha=.6,
                                    grid=True,
                                    colorbar=True,
                                    hover=True,
                                    tools=["crosshair","pan"], 
                                    attr_labels=False, 
                                    height=350)
comm_cumprod_re = (1+comm_daily).cumprod()-1
comm_cumprod_re_plot = comm_cumprod_re.hvplot(shared_axes=False,
                                              title="Communication Cumulative Return",
                                              hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                              hover_alpha=.6,
                                              grid=True,
                                              colorbar=True,
                                              hover=True,
                                              tools=["crosshair","pan"], 
                                              attr_labels=False, 
                                              height=350)
comm_rolling_plot = comm_daily.rolling(window=30).std().hvplot(shared_axes=False,
                                                               title="Communication Rolling Plot",
                                                               hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                                               hover_alpha=.6,
                                                               grid=True,
                                                               colorbar=True,
                                                               hover=True,
                                                               tools=["crosshair","pan"], 
                                                               attr_labels=False, 
                                                               height=350)
comm_sharpe_ratio = (comm_daily.mean()*252)/(comm_daily.std()*np.sqrt(252))
comm_sharpe_ratio_plot = health_care_sharpe_ratio.hvplot.bar(shared_axes=False,
                                                             title="Communication Sharpe Ratio",
                                                             hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                                             hover_alpha=.6,
                                                             grid=True,
                                                             colorbar=True,
                                                             hover=True,
                                                             tools=["crosshair","pan"], 
                                                             attr_labels=False, 
                                                             height=350)
comm_daily_mean = comm_daily.mean()
comm_daily_std = comm_daily.std()
comm_risk = comm_daily_std[comm_daily_std>comm_daily_std["IXP"]]
comm_daily_ewm_plot = comm_daily.ewm(halflife=30).std().hvplot(shared_axes=False,
                                                               title="Communication Exponentially Weighted Moving Avg",
                                                               hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                                               hover_alpha=.6,
                                                               grid=True,
                                                               colorbar=True,
                                                               hover=True,
                                                               tools=["crosshair","pan"], 
                                                               attr_labels=False, 
                                                               height=350)

### -------Monte Carlo--------

# ```Health Care Monte Carlo```

In [18]:
number_simulations = 1000
number_records = 252
sim_health_df = pd.DataFrame()

for i in range(number_simulations):
    sim_UNH_list = [Health_care_df["UNH"][-1]]
    sim_JNJ_list = [Health_care_df["JNJ"][-1]]
    sim_MRK_list = [Health_care_df["MRK"][-1]]
    sim_ABBV_list = [Health_care_df["ABBV"][-1]]
    sim_ABT_list = [Health_care_df["ABT"][-1]]
    sim_XLV_list = [Health_care_df["XLV"][-1]]
    for n in range(number_records):
        sim_UNH_price = sim_UNH_list[-1] * (1 + np.random.normal(health_care_daily_mean["UNH"], health_care_daily_std["UNH"]))
        sim_JNJ_price = sim_JNJ_list[-1]*(1+np.random.normal(health_care_daily_mean["JNJ"], health_care_daily_std["JNJ"]))
        sim_MRK_price = sim_MRK_list[-1]*(1+np.random.normal(health_care_daily_mean["MRK"], health_care_daily_std["MRK"]))
        sim_ABBV_price = sim_ABBV_list[-1]*(1+np.random.normal(health_care_daily_mean["ABBV"], health_care_daily_std["ABBV"]))
        sim_ABT_price = sim_ABT_list[-1]*(1+np.random.normal(health_care_daily_mean["ABT"], health_care_daily_std["ABT"]))
        sim_XLV_price = sim_XLV_list[-1]*(1+np.random.normal(health_care_daily_mean["XLV"], health_care_daily_std["XLV"]))
        sim_UNH_list.append(sim_UNH_price)
        sim_JNJ_list.append(sim_JNJ_price)
        sim_MRK_list.append(sim_MRK_price)
        sim_ABBV_list.append(sim_ABBV_price)
        sim_ABT_list.append(sim_ABT_price)
        sim_XLV_list.append(sim_XLV_price)
    sim_health_df["UNH"] = pd.Series(sim_UNH_list)
    sim_health_df["JNJ"]= pd.Series(sim_JNJ_list)
    sim_health_df["MRK"]=pd.Series(sim_MRK_list)
    sim_health_df["ABBV"]=pd.Series(sim_ABBV_list)
    sim_health_df["ABT"]=pd.Series(sim_ABT_list)
    sim_health_df["XLV"]=pd.Series(sim_XLV_list)    

In [19]:
sim_health_df_plot = sim_health_df.hvplot(shared_axes=False,
                                          title="Health Care Monte Carlo Predicated Future Price",
                                          hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                          hover_alpha=.6,
                                          grid=True,
                                          colorbar=True,
                                          hover=True,
                                          tools=["crosshair","pan"], 
                                          attr_labels=False, 
                                          height=350)
sim_health_df_PCT_plot = sim_health_df.pct_change().hvplot(shared_axes=False,
                                                           title="Health Care Monte Carlo Percent Change",
                                                           hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                                           hover_alpha=.6,
                                                           grid=True,
                                                           colorbar=True,
                                                           hover=True,
                                                           tools=["crosshair","pan"], 
                                                           attr_labels=False, 
                                                           height=350)

# ```Communication Monte Carlo```

In [20]:
number_simulations = 1000
number_records = 252
sim_comm_df = pd.DataFrame()
for i in range(number_simulations):
    sim_CMSA_list = [Communication_df["CMSA"][-1]]  
    sim_BIDU_list = [Communication_df["BIDU"][-1]]
    sim_DISH_list=[Communication_df["DISH"][-1]]
    sim_TMUS_list=[Communication_df["TMUS"][-1]]
    sim_ZM_list=[Communication_df["ZM"][-1]]
    sim_IXP_list=[Communication_df["IXP"][-1]]
    for n in range(number_records):
        sim_CMSA_price = sim_CMSA_list[-1] * (1 + np.random.normal(comm_daily_mean["CMSA"],comm_daily_std["CMSA"]))
        sim_BIDU_price = sim_BIDU_list[-1] * (1 + np.random.normal(comm_daily_mean["BIDU"],comm_daily_std["BIDU"]))
        sim_DISH_price = sim_DISH_list[-1] * (1 + np.random.normal(comm_daily_mean["DISH"],comm_daily_std["DISH"]))
        sim_TMUS_price = sim_TMUS_list[-1] * (1 + np.random.normal(comm_daily_mean["TMUS"],comm_daily_std["TMUS"]))
        sim_ZM_price = sim_ZM_list[-1] * (1 + np.random.normal(comm_daily_mean["ZM"],comm_daily_std["ZM"]))
        sim_IXP_price = sim_IXP_list[-1] * (1 + np.random.normal(comm_daily_mean["IXP"],comm_daily_std["IXP"]))
        sim_CMSA_list.append(sim_CMSA_price)
        sim_BIDU_list.append(sim_BIDU_price)
        sim_DISH_list.append(sim_DISH_price)
        sim_TMUS_list.append(sim_TMUS_price)
        sim_ZM_list.append(sim_ZM_price)
        sim_IXP_list.append(sim_IXP_price)
    sim_comm_df["CMSA"]=pd.Series(sim_CMSA_list)
    sim_comm_df["BIDU"]=pd.Series(sim_BIDU_list)
    sim_comm_df["DISH"]=pd.Series(sim_DISH_list)
    sim_comm_df["TMUS"]=pd.Series(sim_TMUS_list)
    sim_comm_df["ZM"]=pd.Series(sim_ZM_list)
    sim_comm_df["IXP"]=pd.Series(sim_IXP_list)

In [21]:
sim_comm_df_plot = sim_comm_df.hvplot(shared_axes=False,
                                      title="Communication Monte Carlo Predicated Future Price",
                                      hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                      hover_alpha=.6,
                                      grid=True,
                                      colorbar=True,
                                      hover=True,
                                      tools=["crosshair","pan"], 
                                      attr_labels=False, 
                                      height=350)
sim_comm_df_PCT_plot = sim_comm_df.pct_change().hvplot(shared_axes=False,
                                                       title="Communication Monte Carlo Percent Change",
                                                       hover_color=["goldenrod","red","darkblue","chocolate","seagreen","silver"],
                                                       hover_alpha=.6,
                                                       grid=True,
                                                       colorbar=True,
                                                       hover=True,
                                                       tools=["crosshair","pan"], 
                                                       attr_labels=False, 
                                                       height=350)

In [22]:
T1R1 = pn.Row(comm_df_plot,health_care_df_plot)
T1R2 = pn.Row(comm_daily_plot,health_care_daily_plot)
tab1 = pn.Column(T1R1,T1R2)
T2R1= pn.Row(JNJ_rolling_beta_plot)
T2R2 = pn.Row(comm_rolling_plot,health_rolling_window_plot)
T2R2 = pn.Row(comm_cumprod_re_plot,health_cumprod_re_plot)
tab2 = pn.Column(T2R1,T2R2)
tab3 = pn.Column(comm_daily_ewm_plot,health_daily_ewm_plot)
T4R1 = pn.Row(sim_comm_df_plot,sim_health_df_plot)
T4R2 = pn.Row(sim_comm_df_PCT_plot,sim_health_df_PCT_plot)
tab4= pn.Column(T4R1,T4R2)
Sheldon = pn.Tabs(("Prices and Percent Change", tab1),
                 ("Rolling Plots and Cum Returns", tab2),
                 ("Exponentially Weighted Moving Avg", tab3),
                 ("Monte Carlo Simulations", tab4))

In [23]:
covid_data = Path("covid-19-data/us.csv")
covid_df = pd.read_csv(covid_data, index_col='date', parse_dates=True)
covid_df.head()
covid_plot = covid_df.hvplot(title = "Covid Data", shared_axes=False)

covid_pct_change = covid_df.pct_change()
covid_pct_change_plot = covid_pct_change.hvplot(title = "Covid Percent Change", shared_axes=False)
ent_stocks_pct_change = ent_stocks_pct_change.drop(columns="xly")
res_stocks_pct_change=res_stocks_pct_change.drop(columns="xly")
combined_pct_change = pd.concat([covid_pct_change, tech_stocks_daily_returns,
                                 health_care_daily,comm_daily,ent_stocks_pct_change,hot_stocks_pct_change,res_stocks_pct_change], axis = 'columns', join= 'inner')
combined_pct_change_plot = combined_pct_change.fillna(0).hvplot(title = "Covid Percent Change Over Stock Daily Returns", 
                                                                shared_axes=False, 
                                                                hover_alpha=.6,
                                                                grid=True,
                                                                colorbar=True,
                                                                hover=True,
                                                                tools=["crosshair","pan"], 
                                                                attr_labels=False, 
                                                                height=600,
                                                                width=1200)


In [24]:
project=pn.Tabs(("Intro", combined_pct_change_plot),
               ("Sheldon", Sheldon),
               ("Xavier", Xavier),
               ("Richard", Richard))

In [25]:
project

Tabs
    [0] HoloViews(NdOverlay, name='Intro')
    [1] Tabs
        [0] Column
            [0] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
            [1] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
        [1] Column
            [0] Row
                [0] HoloViews(Curve)
            [1] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
        [2] Column
            [0] HoloViews(NdOverlay)
            [1] HoloViews(NdOverlay)
        [3] Column
            [0] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
            [1] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
    [2] Tabs
        [0] Column
            [0] HoloViews(NdOverlay)
        [1] Column
            [0] HoloViews(NdOverlay)
        [2] Column
            [0] HoloViews(NdOverlay)
        [3] Column
            [0] HoloViews(NdOverlay)
        [4] Column
            [0] HoloViews(NdOverlay)
        [5] Column
            [0] HoloViews(NdOverlay)
        [6] Column
            [0] HoloViews(Curve)
    [3] Tabs
        [0] Column
            [0] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
            [1] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
        [1] Column
            [0] HoloViews(Curve)
            [1] Row
                [0] HoloViews(Overlay)
                [1] HoloViews(Overlay)
            [2] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
        [2] Column
            [0] HoloViews(NdOverlay)
            [1] HoloViews(NdOverlay)
        [3] Column
            [0] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
            [1] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)
            [2] Row
                [0] HoloViews(NdOverlay)
                [1] HoloViews(NdOverlay)